In [39]:
import codecs
import networkx as nx
import os
import pandas as pd
import pickle
import re
from difflib import SequenceMatcher
from os import listdir
from os.path import isfile, join
from networkx.algorithms import isomorphism
from networkx.drawing.nx_pydot import write_dot
from utils import printProgressBar

# AOC-posets from max graph
## Compare complete extent size (for missing lexemes)

In [ ]:
frequencies = pd.read_csv('frequencies-frcowvec-filtered.csv', header=0, index_col=0)
frequencies.shape

In [3]:
ignored = ['F06082', 'F06086', 'F06138', 'F04553', 'F04843', 'F04879', 'F04942', 'F04945', 'F05607', 'F05702', 'F05920', 'F05956', 'F05989', 'F05963', 'F06003', 'F06020', 'F06027', 'F06030', 'F06032', 'F06038', 'F06048', 'F06049', 'F06050', 'F06067', 'F06072', 'F06085', 'F06102', 'F06127', 'F06129', 'F06139', 'F06165', 'F06167', 'F06168', 'F06188', 'F06192', 'F06197']
graph_filenames = list()
graph_binary_filenames = list()
for f in listdir('demonette-glawinette_graph'):
    if isfile(join('demonette-glawinette_graph', f)):
        if f.split()[0] not in ignored:
            graph_filenames.append(f)
for f in listdir('demonette-glawinette_graph_binary'):
    if isfile(join('demonette-glawinette_graph_binary', f)):
        if f not in ignored:
            graph_binary_filenames.append(f)
graph_filenames.sort()
graph_binary_filenames.sort()

In [5]:
full_extent_dict = dict()
with codecs.open(join('demonette-glawinette_posets', 'maxgraph_full.dot'), 'r', encoding='utf-8') as f:
    for line in f:
        if 'Attribute' in line:
            full_extent_dict[line.split()[0]] = set(line.replace('Object ', '').split('|')[-1].split('\\n')[:-1])
        elif '->' in line:
            break
            
L = nx.DiGraph()
with codecs.open(join('demonette-glawinette_posets', 'maxgraph_simplified.dot'), 'r', encoding='utf-8') as f:
    for line in f:
        if '->' in line:
            v = line.split()
            L.add_edge(v[2], v[0])
        elif 'Attribute' in line:
            vertex_id = line.split()[0]
            #introduced_intent = col_names[int(line.split('|')[1].replace('Attribute ', '').replace('\\n', ''))]
            introduced_extent = line.replace('Object ', '').split('|')[-1].split('\\n')[:-1]
            extent_size = re.search('E: (.*)\)', line).group(1)
            L.add_node(vertex_id, introduced_intent=int(line.split('|')[1].replace('Attribute ', '').replace('\\n', '')),\
                       extent_size=extent_size, introduced_extent=introduced_extent,\
                       concept_number=re.search('<(.*)>', line).group(1))

In [46]:
def generate_lexeme(a1, a2, b1):
    a1_lex = '{' + a1.split('_')[0] + '}'
    a2_lex = '{' + a2.split('_')[0] + '}'
    b1_lex = '{' + b1.split('_')[0] + '}'
    a2_cat = a2.split('_')[1]
    match = SequenceMatcher(None, a1_lex, a2_lex).find_longest_match(0, len(a1_lex), 0, len(a2_lex))
    common = a1_lex[match.a:match.a+match.size]
    a1_suffix = a1_lex.replace(common, '')
    a2_suffix = a2_lex.replace(common, '')
    b2_lex = b1_lex.replace(a1_suffix, a2_suffix)
    if b2_lex == b1_lex and a1_lex != a2_lex:
        return 'XX'
    return b2_lex.replace('{', '').replace('}', '') + '_' + a2_cat

def prediction(G_parent, G_child, C_parent, C_child):
    GM = isomorphism.DiGraphMatcher(G_child, G_parent, node_match=lambda v1,v2: v1['label'] == v2['label'], edge_match=lambda e1,e2: e1['label'] == e2['label'])
    node_diff = set()
    matching_count = 0
    for subgraph in GM.subgraph_isomorphisms_iter():
        # subgraph => {'héraclitien_Adj': 'élyséen_Adj', 'Héraclite_Npx': 'Elysée_Npx', 'héraclitéen_Nm': 'élyséen_Nm'}
        matching_count += 1
        node_diff = G_child.nodes - subgraph
    # node_diff => {'héraclitéen_Adj'}
    if matching_count > 1:
        return '??'
    ret_str = ''
    for n in node_diff:
        homograph = ''
        for key in subgraph:
            if key.split('_')[0] == n.split('_')[0]:
                homograph = key
                break
        if homograph != '':
            ret_str += subgraph.get(key).split('_')[0] + '_' + n.split('_')[1] + ', '
        else:
            for key in subgraph:
                print(generate_lexeme(key, n, subgraph.get(key)))
            #print(nx.descendants(L, C_child))
    return ret_str[:-2]

In [47]:
G_parent = pickle.load(open(join('demonette-glawinette_graph_binary', 'F06911-2'), 'rb'))
one_G_child = pickle.load(open(join('demonette-glawinette_graph_binary', 'F03139'), 'rb'))
prediction(G_parent, one_G_child, '1956415355', '940857381')

déler_V
déler_V
déler_V


''

In [33]:
vertices = list(L.nodes)
edge_counter = 0
L_size = L.size()
binary_dir = 'demonette-glawinette_graph_binary'
df_lattice = pd.DataFrame(columns=['concept_pair', 'parent_ext', 'child_ext', 'ext_ratio', 'ante_node_count',
                                   'cons_node_count', 'missing_node_count', 'parent', 'child', 'missing'])
for vertex in vertices:
#     if vertex != '1971152916':
#         continue
    current_extent_size = int(L.nodes[vertex]['extent_size'])
    G_parent = pickle.load(open(join(binary_dir, graph_binary_filenames[int(L.nodes[vertex]['introduced_extent'][0])]), 'rb'))
    current_graph_len = len(G_parent)
    children = L.neighbors(vertex)
    for child in children:
        edge_counter += 1
        printProgressBar(edge_counter, L_size, prefix = 'Progress:', suffix = 'complete', length = 50, decimals = 2)
        ext_ratio = int(L.nodes[child]['extent_size']) / current_extent_size
        if ext_ratio < 0.8:
            continue
        one_introduced_extent = L.nodes[child]['introduced_extent'][0]
        one_G_child = pickle.load(open(join(binary_dir, graph_binary_filenames[int(one_introduced_extent)]), 'rb'))
        child_graph_len = len(one_G_child)
        node_count_diff = child_graph_len - current_graph_len
        if node_count_diff > 1:
            continue
        concept_pair = L.nodes[vertex]['concept_number'] + '-' + L.nodes[child]['concept_number']
        introduced_extent = set(L.nodes[vertex]['introduced_extent'])
        for e in introduced_extent:
            G_parent = pickle.load(open(join(binary_dir, graph_binary_filenames[int(e)]), 'rb'))
            df_lattice = df_lattice.append(pd.Series({
                    'parent': '=HYPERLINK("demonette-glawinette_graph\\' + graph_filenames[int(e)] + '", "' + graph_filenames[int(e)] + ' **")',
                    'child': '=HYPERLINK("demonette-glawinette_graph\\' + graph_filenames[int(one_introduced_extent)] + '", "' + graph_filenames[int(one_introduced_extent)] + '")',
                    'parent_ext': current_extent_size,
                    'child_ext': int(L.nodes[child]['extent_size']),
                    'ext_ratio': ext_ratio,
                    'ante_node_count': current_graph_len,
                    'cons_node_count': child_graph_len,
                    'missing_node_count': node_count_diff,
                    'missing': prediction(G_parent, one_G_child, vertex, child),
                    'concept_pair': concept_pair
                }), ignore_index=True)
        
        extent_diff = full_extent_dict[vertex] - full_extent_dict[child] - introduced_extent
        for e in extent_diff:
            G_sibling = pickle.load(open(join(binary_dir, graph_binary_filenames[int(e)]), 'rb'))
            df_lattice = df_lattice.append(pd.Series({
                    'parent': '=HYPERLINK("demonette-glawinette_graph\\' + graph_filenames[int(e)] + '", "' + graph_filenames[int(e)] + '")',
                    'child': '=HYPERLINK("demonette-glawinette_graph\\' + graph_filenames[int(one_introduced_extent)] + '", "' + graph_filenames[int(one_introduced_extent)] + '")',
                    'parent_ext': current_extent_size,
                    'child_ext': int(L.nodes[child]['extent_size']),
                    'ext_ratio': ext_ratio,
                    'ante_node_count': current_graph_len,
                    'cons_node_count': child_graph_len,
                    'missing_node_count': node_count_diff,
                    'missing': '',
                    'concept_pair': concept_pair 
                }), ignore_index=True)

Progress: |██------------------------------------------------| 5.15% complete

Progress: |████████████████████------------------------------| 41.33% complete

Progress: |██████████████████████████████████████████████████| 100.00% complete


In [34]:
df_lattice.to_excel('DG-missing.xlsx', index=False)